тут мы загрузили наши данный и залили в dataFrame при помощи lib pandas

In [2]:
import numpy as np
import csv
import pandas as pd
import matplotlib.pyplot as plt

from sklearn.model_selection import train_test_split

data = pd.read_csv("C:\\git_boris\\demo\\my_projects\\ML\\organisations.csv")
features = pd.read_csv("C:\\git_boris\\demo\\my_projects\\ML\\features.csv")
rubrics = pd.read_csv("C:\\git_boris\\demo\\my_projects\\ML\\rubrics.csv")

# Используем метод head() для объекта DataFrame
# print(data.head())
feature_dict = pd.Series(features.feature_name.values, 
                         index=features.feature_id).to_dict()
rubric_dict = pd.Series(rubrics.rubric_name.values, 
                        index=rubrics.rubric_id).to_dict()

#task1
data.dropna(subset="average_bill")
clean_data = data[data["average_bill"] <= 2500]

первый класификатор: бейзлайн, а точнее среднее арифмитическое таргета

In [3]:
from sklearn.model_selection import train_test_split
from scipy.stats import mode
from sklearn.base import RegressorMixin

class MeanRegressor(RegressorMixin):
    def __init__(self):
        self.mean = 0
    # Predicts the mean of y_train
    def fit(self, X=None, y=None):
        '''
        Parameters
        ----------
        X : array like, shape = (n_samples, n_features)
        Training data features
        y : array like, shape = (_samples,)
        Training data targets
        '''
        self.mean = np.mean(y)
        return self
        

    def predict(self, X=None):
        '''
        Parameters
        ----------
        X : array like, shape = (n_samples, n_features)
        Data to predict
        '''
        return np.full(shape = (X.shape[0],), fill_value = self.mean)

from sklearn.base import ClassifierMixin



class MostFrequentClassifier(ClassifierMixin):
    def __init__(self):
        self.popular_mean = 0
    # Predicts the rounded (just in case) median of y_train
    def fit(self, X=None, y=None):
        '''
        Parameters
        ----------
        X : array like, shape = (n_samples, n_features)
        Training data features
        y : array like, shape = (_samples,)
        Training data targets
        '''
        self.popular_mean = mode(y).mode[0]
        return self

    def predict(self, X=None):
        '''
        Parameters
        ----------
        X : array like, shape = (n_samples, n_features)
        Data to predict
        '''
        return np.full(shape=(X.shape[0],), fill_value = self.popular_mean)
    
clean_data_train, clean_data_test = train_test_split(clean_data, stratify=clean_data['average_bill'], test_size=0.33, random_state=42)
    
reg = MeanRegressor()
reg.fit(y=clean_data_train['average_bill'])


from sklearn.metrics import mean_squared_error
predictions = reg.predict(clean_data_test['average_bill'])

# Evaluate the model
rmse = np.sqrt(mean_squared_error(clean_data_test['average_bill'], predictions))
print(f"RMSE для регрессионной модели: {rmse}")

RMSE для регрессионной модели: 448.7143889551622


тут уже класификатор посложнее будет

во первых мы будем использовать концепцию зоведения (бар, кафе, ресторан) НО! одно заведения может включать себе несколько рубрик
поэтому если с такой комбинацией рубрик <100 заведений, мы придаем ему значение other(-1)

а потом мы групируем по городу и рубрикам и находим среднее этих групп

In [4]:
from collections import Counter

rubric_arr = clean_data['rubrics_id']
my_counter = Counter(rubric_arr)

# Using list comprehension for a more concise approach
modified_rubrics = [0 if my_counter[el] < 100 else el for el in rubric_arr]

# clean_data['modified_rubrics'] = modified_rubrics

# clean_data_train, clean_data_test = train_test_split(clean_data, stratify=clean_data['average_bill'], test_size=0.33, random_state=42)

import pandas as pd
from sklearn.base import ClassifierMixin

class RubricCityMedianClassifier(ClassifierMixin):
    def __init__(self):
        self.counter = dict()
    
    def fit(self, X=None, y=None):
        data = X.copy()
        data['target'] = y

        groups = data.groupby([ 'modified_rubrics', 'city'])['target'].median()
        self.counter = groups.to_dict()
        return self

    def predict(self, X=None):
        predictions = [self.counter[(row['modified_rubrics'] , row['city'])] for index, row in X.iterrows()]
        return predictions


# regCity = RubricCityMedianClassifier()
# regCity.fit(X=clean_data_train, y=clean_data_train['average_bill'])

# Прогнозирование
# predictions = regCity.predict(clean_data_test)

# Оценка модели
# rmse1 = np.sqrt(mean_squared_error(clean_data_test['average_bill'], predictions))
# print(f"RMSE для регрессионной модели: {rmse1}")

моделька по рубрекам и фичам заведения

In [5]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.base import BaseEstimator, ClassifierMixin
import csv

clean_data['modified_features'] = clean_data["rubrics_id"].astype(str) + 'q' + clean_data['features_id'].astype(str)

clean_data_train, clean_data_test = train_test_split(clean_data, stratify=clean_data['average_bill'], test_size=0.33, random_state=42)

# Инициализация уникальных значений
unique_f = clean_data_train['modified_features'].unique()
clean_data_test['modified_features'] = clean_data_test['modified_features'].apply(lambda x: x if x in unique_f else 'other')

global_median = clean_data_train['average_bill'].median()

# Пользовательский классификатор
class RubricCityMedianClassifier(BaseEstimator, ClassifierMixin):
    def __init__(self):
        self.counter = dict()
        self.global_median = global_median

    def fit(self, X, y):
        data = X.copy()
        data['target'] = y
        
        groups = data.groupby(['modified_features'])['target'].median()
        self.counter = groups.to_dict()
        return self

    def predict(self, X):
        predictions = []
        for index, row in X.iterrows():
            prediction = self.counter.get(row['modified_features'], self.global_median)  # Используем global_median, если не найдено
            predictions.append(int(prediction))    
        return predictions

# Instantiate and fit the classifier
classifier = RubricCityMedianClassifier()
classifier.fit(clean_data_train[['modified_features']], clean_data_train['average_bill'])

# Predict on training and testing sets
predictionsTrain = classifier.predict(clean_data_train[['modified_features']])
predictionsTest = classifier.predict(clean_data_test[['modified_features']])

rmseTrain = np.sqrt(mean_squared_error(clean_data_train['average_bill'], predictionsTrain))
rmseTest = np.sqrt(mean_squared_error(clean_data_test['average_bill'], predictionsTest))

# Output RMSE results
print(f'RMSE for Training Set: {round(rmseTrain, 2)}')
print(f'RMSE for Testing Set: {round(rmseTest, 2)}')

from sklearn.metrics import balanced_accuracy_score

scoreTrain = balanced_accuracy_score(clean_data_train['average_bill'], predictionsTrain)
scoreTest = balanced_accuracy_score(clean_data_test['average_bill'], predictionsTest)

print(f'balanced_accuracy_score for Training Set: {round(scoreTrain, 2)}')
print(f'balanced_accuracy_score for Testing Set: {round(scoreTest, 2)}')

# Создание DataFrame из предсказаний
# dataframe = pd.DataFrame(predictions)

# Сохранение в CSV без кавычек
# dataframe.to_csv('unser.csv', index=False, header=False, quoting=csv.QUOTE_NONE, escapechar='\\')


C:\Users\krutko_kay\AppData\Local\Temp\ipykernel_5988\22209765.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  clean_data['modified_features'] = clean_data["rubrics_id"].astype(str) + 'q' + clean_data['features_id'].astype(str)


RMSE for Training Set: 32.42
RMSE for Testing Set: 513.99
balanced_accuracy_score for Training Set: 0.99
balanced_accuracy_score for Testing Set: 0.2


C:\Users\krutko_kay\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\LocalCache\local-packages\Python311\site-packages\sklearn\metrics\_classification.py:2480: UserWarning: y_pred contains classes not in y_true
  warnings.warn("y_pred contains classes not in y_true")
C:\Users\krutko_kay\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\LocalCache\local-packages\Python311\site-packages\sklearn\metrics\_classification.py:2480: UserWarning: y_pred contains classes not in y_true
  warnings.warn("y_pred contains classes not in y_true")


catboost


In [6]:
data = pd.read_csv("C:\\git_boris\\demo\\my_projects\\ML\\organisations.csv")
features = pd.read_csv("C:\\git_boris\\demo\\my_projects\\ML\\features.csv")
rubrics = pd.read_csv("C:\\git_boris\\demo\\my_projects\\ML\\rubrics.csv")

data.dropna(subset="average_bill")
clean_data = data[data["average_bill"] <= 2500]

feature_list = features['feature_id'].tolist()
rubric_list = rubrics['rubric_id'].tolist()

clean_data_train, clean_data_test = train_test_split(clean_data, stratify=clean_data['average_bill'], test_size=0.33, random_state=42)

indexs = clean_data_train.index.tolist()

data = []
rows = []
columns = []

dict_data_train = clean_data_train.to_dict()
print(dict_data_train)
for ind_row, id in enumerate(indexs, 0):
    ind_col = 0
    # city
    if (dict_data_train['city'][id] == 'msk'):
        data.append(1)
        rows.append(ind_row)
        columns.append(ind_col)
    # rating
    data.append(dict_data_train['rating'][id])
    rows.append(ind_row)
    columns.append(ind_col + 1)
    # rubrics
    for ind_col, rubric in enumerate(rubric_list, 2):
        rubrics = dict_data_train['rubrics_id'][id].split()
        if (rubric in rubrics):
            data.append(1)
            rows.append(ind_row)
            columns.append(ind_col)
    # features
    for ind_col, feature in enumerate(feature_list, len(rubric_list) + 2):
        features = dict_data_train['features_id'][id].split()
        if (feature in features):
            data.append(1)
            rows.append(ind_row)
            columns.append(ind_col)

            
        
        


{'org_id': {45769: 3276960721840719260, 39061: 8452997364765928283, 59281: 14240408259222214074, 51225: 15114069072602161053, 29587: 2730337118800634815, 46706: 16990118229778698146, 49388: 15328432697243413588, 53589: 6311296738926960771, 58056: 13302179954888852449, 37036: 2288802948136770304, 4159: 13289451449529945019, 36219: 12459393615989836151, 42995: 6416781923417689635, 33088: 10501124321232428907, 67442: 3574969689859595350, 27788: 5801028168009004396, 41110: 3978047908762287951, 55190: 15443348602974247560, 37949: 15524954908950797738, 33961: 578113128438152991, 67421: 12363330468286102624, 46942: 5249595100492684754, 45386: 16822803167317175355, 65965: 2703312914795907435, 30192: 7241862512129286326, 58140: 8924284884403753375, 56970: 9221662383398078251, 46145: 5241341496045274947, 51609: 15686090553232986611, 11830: 14536679714755337606, 37505: 11037135946276827385, 60172: 9942274683167703682, 59749: 9809523701922067444, 18521: 17307343719940685159, 58456: 138178800467954

KeyboardInterrupt: 